# Main notebook for battery state estimation

In [1]:
import numpy as np
import pandas as pd
import scipy.io
import math
import os
import ntpath
import sys
import logging
import time
import sys

from importlib import reload
import plotly.graph_objects as go

import tensorflow as tf
from tensorflow import keras
from tensorflow.keras import layers

from keras.models import Sequential
from keras.layers.core import Dense, Dropout, Activation
from keras.optimizers import SGD, Adam
from keras.utils import np_utils
from keras.layers import LSTM, Embedding, RepeatVector, TimeDistributed, Masking
from keras.callbacks import EarlyStopping, ModelCheckpoint, LambdaCallback


IS_COLAB = False

if IS_COLAB:
    from google.colab import drive
    drive.mount('/content/drive')
    data_path = "/content/drive/My Drive/battery-state-estimation/battery-state-estimation/"
else:
    data_path = "../../../"

sys.path.append(data_path)
from data_processing.unibo_powertools_data import UniboPowertoolsData, CycleCols
from data_processing.model_data_handler import ModelDataHandler

### Config logging

In [2]:
reload(logging)
logging.basicConfig(format='%(asctime)s [%(levelname)s]: %(message)s', level=logging.DEBUG, datefmt='%Y/%m/%d %H:%M:%S')

# Load Data

### Initial the data object

Load the cycle and capacity data to memory based on the specified chunk size

In [3]:
dataset = UniboPowertoolsData(
    test_types=[],
    chunk_size=1000000,
    lines=[37, 40],
    charge_line=37,
    discharge_line=40,
    base_path=data_path
)

2021/01/01 19:05:48 [DEBUG]: Start loading data with lines: [37, 40], types: [] and chunksize: 1000000...
2021/01/01 19:06:06 [DEBUG]: Finish loading data.
2021/01/01 19:06:06 [INFO]: Loaded raw dataset A data with cycle row count: 8485716 and capacity row count: 21604
2021/01/01 19:06:06 [DEBUG]: Start cleaning cycle raw data...
2021/01/01 19:06:10 [DEBUG]: Finish cleaning cycle raw data.
2021/01/01 19:06:10 [INFO]: Removed 11 rows of abnormal cycle raw data.
2021/01/01 19:06:10 [DEBUG]: Start cleaning capacity raw data...
2021/01/01 19:06:10 [DEBUG]: Finish cleaning capacity raw data.
2021/01/01 19:06:10 [INFO]: Removed 1 rows of abnormal capacity raw data.
2021/01/01 19:06:10 [DEBUG]: Start assigning charging raw data...
2021/01/01 19:06:11 [DEBUG]: Finish assigning charging raw data.
2021/01/01 19:06:11 [INFO]: [Charging] cycle raw count: 6671942, capacity raw count: 10804
2021/01/01 19:06:11 [DEBUG]: Start assigning discharging raw data...
2021/01/01 19:06:11 [DEBUG]: Finish assig

### Determine the training and testing name

Prepare the training and testing data for model data handler to load the model input and output data.

In [4]:
train_data_test_names = [
    '000-DM-3.0-4019-S',  
    '001-DM-3.0-4019-S',  
    '002-DM-3.0-4019-S', 

    '006-EE-2.85-0820-S', 
    '007-EE-2.85-0820-S',
    '042-EE-2.85-0820-S',

    '009-DM-3.0-4019-H',  
    '010-DM-3.0-4019-H',

    '013-DM-3.0-4019-P',  
    '014-DM-3.0-4019-P',
    '015-DM-3.0-4019-P',  
    '016-DM-3.0-4019-P', 

    '018-DP-2.00-1320-S', 
    '019-DP-2.00-1320-S', 
    '036-DP-2.00-1720-S',
    '037-DP-2.00-1720-S', 
    '038-DP-2.00-2420-S',

    '043-EE-2.85-0820-H',
    
    #'040-DM-4.00-2320-S', 
    #'045-BE-2.75-2019-S'
]

test_data_test_names = [
    '003-DM-3.0-4019-S', 
    '008-EE-2.85-0820-S', 
    '011-DM-3.0-4019-H', 
    '017-DM-3.0-4019-P', 
    '039-DP-2.00-2420-S',
    '044-EE-2.85-0820-H',
    
    #'041-DM-4.00-2320-S',
]

dataset.prepare_data(train_data_test_names, test_data_test_names)

2021/01/01 19:06:11 [DEBUG]: Start preparing data for training: ['000-DM-3.0-4019-S', '001-DM-3.0-4019-S', '002-DM-3.0-4019-S', '006-EE-2.85-0820-S', '007-EE-2.85-0820-S', '042-EE-2.85-0820-S', '009-DM-3.0-4019-H', '010-DM-3.0-4019-H', '013-DM-3.0-4019-P', '014-DM-3.0-4019-P', '015-DM-3.0-4019-P', '016-DM-3.0-4019-P', '018-DP-2.00-1320-S', '019-DP-2.00-1320-S', '036-DP-2.00-1720-S', '037-DP-2.00-1720-S', '038-DP-2.00-2420-S', '043-EE-2.85-0820-H'] and testing: ['003-DM-3.0-4019-S', '008-EE-2.85-0820-S', '011-DM-3.0-4019-H', '017-DM-3.0-4019-P', '039-DP-2.00-2420-S', '044-EE-2.85-0820-H']...
2021/01/01 19:06:26 [DEBUG]: Finish getting training and testing charge data.
2021/01/01 19:06:37 [DEBUG]: Finish getting training and testing discharge data.
2021/01/01 19:06:37 [DEBUG]: Finish cleaning training and testing charge data.
2021/01/01 19:06:37 [DEBUG]: Finish cleaning training and testing discharge data.
2021/01/01 19:06:39 [DEBUG]: Finish adding training and testing discharge SOC para

### Initial the model data handler

Model data handler will be used to get the model input and output data for further training purpose.

In [5]:
mdh = ModelDataHandler(dataset, [
    CycleCols.VOLTAGE,
    CycleCols.CURRENT,
    CycleCols.TEMPERATURE
])

# Data loading

In [6]:
train_x, train_y, test_x, test_y = mdh.get_discharge_whole_cycle(soh = False, output_capacity = False)

2021/01/01 19:06:50 [INFO]: Train x: (7607, 215, 3), train y: (7607, 215, 2) | Test x: (2294, 215, 3), test y: (2294, 215, 2)


In [7]:
train_y = mdh.keep_only_capacity(train_y, is_multiple_output = True)
test_y = mdh.keep_only_capacity(test_y, is_multiple_output = True)

2021/01/01 19:06:50 [INFO]: New y: (7607, 215)
2021/01/01 19:06:50 [INFO]: New y: (2294, 215)


In [8]:
# Model definition

#opt = tf.keras.optimizers.Adam(lr=0.00003)

#model = Sequential()
#model.add(LSTM(256, activation='selu',
#                return_sequences=True,
#                input_shape=(train_x.shape[1], train_x.shape[2])))
#model.add(LSTM(256, activation='selu', return_sequences=True))
#model.add(LSTM(128, activation='selu', return_sequences=True))
#model.add(Dense(64, activation='selu'))
#model.add(Dense(1, activation='linear'))
#model.summary()

#model.compile(optimizer=opt, loss='huber', metrics=['mse', 'mae', 'mape', tf.keras.metrics.RootMeanSquaredError(name='rmse')])

In [9]:
experiment_name = '2020-12-31-16-48-12_lstm_soc_percentage_all_sufficient_types'

history = pd.read_csv(data_path + 'results/trained_model/%s_history.csv' % experiment_name)
model = keras.models.load_model(data_path + 'results/trained_model/%s.h5' % experiment_name)
model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm (LSTM)                  (None, 215, 256)          266240    
_________________________________________________________________
lstm_1 (LSTM)                (None, 215, 256)          525312    
_________________________________________________________________
lstm_2 (LSTM)                (None, 215, 128)          197120    
_________________________________________________________________
dense (Dense)                (None, 215, 64)           8256      
_________________________________________________________________
dense_1 (Dense)              (None, 215, 1)            65        
Total params: 996,993
Trainable params: 996,993
Non-trainable params: 0
_________________________________________________________________


In [10]:
print(history)

     Unnamed: 0      loss       mse       mae          mape      rmse  \
0             0  0.011250  0.022541  0.063172  7.609676e+06  0.150138   
1             1  0.004101  0.008201  0.033840  2.197540e+06  0.090561   
2             2  0.002959  0.005918  0.030072  2.152436e+06  0.076926   
3             3  0.002330  0.004660  0.028517  2.312790e+06  0.068267   
4             4  0.001735  0.003469  0.022504  1.540559e+06  0.058901   
..          ...       ...       ...       ...           ...       ...   
187         187  0.000015  0.000031  0.003907  4.186132e+05  0.005555   
188         188  0.000016  0.000032  0.004063  4.970074e+05  0.005661   
189         189  0.000015  0.000030  0.003850  4.343053e+05  0.005435   
190         190  0.000022  0.000044  0.004819  5.658377e+05  0.006643   
191         191  0.000018  0.000036  0.004099  4.590178e+05  0.005961   

     val_loss   val_mse   val_mae      val_mape  val_rmse  
0    0.005374  0.010748  0.043693  3.122848e+06  0.103675  
1  

In [11]:
results = model.evaluate(test_x, test_y)
print(results)

72/72 [==============================] - 7s 98ms/step - loss: 8.1438e-05 - mean_squared_error: 1.6288e-04 - mean_absolute_error: 0.0061 - mean_absolute_percentage_error: 543900.3750 - rmse: 0.0128
[8.143796003423631e-05, 0.00016287592006847262, 0.006051202304661274, 543900.375, 0.012762283906340599]


# Data Visualization

In [12]:
fig = go.Figure()
fig.add_trace(go.Scatter(y=history['loss'],
                    mode='lines', name='train'))
fig.add_trace(go.Scatter(y=history['val_loss'],
                    mode='lines', name='validation'))
fig.update_layout(title='Loss trend',
                  xaxis_title='epoch',
                  yaxis_title='loss',
                  width=1400,
                  height=600)
fig.show()

In [13]:
train_predictions = model.predict(train_x)

In [14]:
cycle_num = 10
steps_num = 10000
step_index = np.arange(cycle_num*steps_num, (cycle_num+1)*steps_num)

fig = go.Figure()
fig.add_trace(go.Scatter(x=step_index, y=train_predictions.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC predicted'))
fig.add_trace(go.Scatter(x=step_index, y=train_y.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC actual'))
fig.update_layout(title='Results on training',
                  xaxis_title='Cycle',
                  yaxis_title='Percentage',
                  width=1400,
                  height=600)
fig.show()

In [15]:
cycle_num = 100
steps_num = 10000
step_index = np.arange(cycle_num*steps_num, (cycle_num+1)*steps_num)

fig = go.Figure()
fig.add_trace(go.Scatter(x=step_index, y=train_predictions.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC predicted'))
fig.add_trace(go.Scatter(x=step_index, y=train_y.flatten()[cycle_num*steps_num:(cycle_num+1)*steps_num],
                    mode='lines', name='SoC actual'))
fig.update_layout(title='Results on training',
                  xaxis_title='Cycle',
                  yaxis_title='Percentage',
                  width=1400,
                  height=600)
fig.show()

# Testing

In [16]:
def plot_test_results(test_index, next_test_index, test_name):
    
    print(test_name + ':')
    
    test_x_under_test_name = test_x[test_index:next_test_index]
    test_y_under_test_name = test_y[test_index:next_test_index]    
    print(model.evaluate(test_x_under_test_name, test_y_under_test_name))
    
    # Remove zero-padded value in cycle end...
    max_index = np.argmax(test_y[test_index] <= 0)
    if(max_index == 0):
        max_index = test_y[test_index].shape[0] 
    test_predictions = model.predict(test_x[test_index:test_index+1])
    
    fig = go.Figure()
    fig.add_trace(go.Scatter(y=test_predictions[0][:max_index,0], mode='lines', name='SoC predicted'))
    fig.add_trace(go.Scatter(y=test_y[test_index][:max_index], mode='lines', name='SoC actual'))
    fig.update_layout(title='Results on testing of ' + test_name,
                      xaxis_title='Cycle',
                      yaxis_title='SoC percentage')
    fig.show()

In [17]:
# Get corresponding cycle index of each test name
indecies = list()
train_discharge_cyc,train_discharge_cap,test_discharge_cyc,test_discharge_cap = dataset.get_discharge_data()
for name in test_data_test_names:
    indecies.append(np.argmax(test_discharge_cap[:,0] == name))

In [18]:
for i in range(len(indecies)):
    if(i == len(indecies)-1):
        plot_test_results(indecies[i], -1, test_data_test_names[i])
    else:
        plot_test_results(indecies[i], indecies[i+1], test_data_test_names[i])        

003-DM-3.0-4019-S:
12/12 [==============================] - 1s 93ms/step - loss: 2.1444e-05 - mean_squared_error: 4.2888e-05 - mean_absolute_error: 0.0050 - mean_absolute_percentage_error: 186094.6719 - rmse: 0.0065
[2.1443805962917395e-05, 4.288761192583479e-05, 0.0049772197380661964, 186094.671875, 0.006548863369971514]


008-EE-2.85-0820-S:
22/22 [==============================] - 2s 92ms/step - loss: 4.9729e-06 - mean_squared_error: 9.9458e-06 - mean_absolute_error: 0.0023 - mean_absolute_percentage_error: 130645.2422 - rmse: 0.0032
[4.972888746124227e-06, 9.945777492248453e-06, 0.0023442485835403204, 130645.2421875, 0.0031536926981061697]


011-DM-3.0-4019-H:
15/15 [==============================] - 1s 89ms/step - loss: 2.9273e-05 - mean_squared_error: 5.8547e-05 - mean_absolute_error: 0.0052 - mean_absolute_percentage_error: 839717.5625 - rmse: 0.0077
[2.9273398467921652e-05, 5.8546796935843304e-05, 0.005160170141607523, 839717.5625, 0.0076515888795256615]


017-DM-3.0-4019-P:
11/11 [==============================] - 1s 92ms/step - loss: 2.9774e-05 - mean_squared_error: 5.9549e-05 - mean_absolute_error: 0.0051 - mean_absolute_percentage_error: 249493.4062 - rmse: 0.0077
[2.977428630401846e-05, 5.954857260803692e-05, 0.005124825984239578, 249493.40625, 0.007716772146522999]


039-DP-2.00-2420-S:
8/8 [==============================] - 1s 91ms/step - loss: 8.1133e-06 - mean_squared_error: 1.6227e-05 - mean_absolute_error: 0.0028 - mean_absolute_percentage_error: 501621.2188 - rmse: 0.0040
[8.113266630971339e-06, 1.6226533261942677e-05, 0.0027859171386808157, 501621.21875, 0.004028216935694218]


044-EE-2.85-0820-H:
6/6 [==============================] - 1s 89ms/step - loss: 7.8147e-04 - mean_squared_error: 0.0016 - mean_absolute_error: 0.0295 - mean_absolute_percentage_error: 2578071.0000 - rmse: 0.0395
[0.0007814711425453424, 0.0015629422850906849, 0.029464056715369225, 2578071.0, 0.0395340658724308]
